In [1]:
from __future__ import division
import numpy as np
import os
import time


# equivalences:
# Python 2       Python 3
# -----------------------
# range(4)       list(range(4))
# xrange(4)      range(4)
try:
    xrange   # fails in Python 3
except NameError:
    xrange = range
    

# reading in knapsack instance:
numOfItems = 20
instanceNumber = 1
# TODO: change path to fit your system and download folder
filename = 'C://users/dimo/desktop/teaching/Saclay2015/introToOptimization/02-dynProgAndBranchBound/knapsackinstances/KP-random-%ditems-%d.txt' % (numOfItems, instanceNumber)
w = []
p = []
with open(filename, "r") as text_file:
        for line in text_file:
            ll = line.split()
            if 'W' in ll[0]:
                W = int(ll[2])
            if 'n' not in ll[0] and 'W' not in ll[0]:
                w.append(int(ll[0]))
                p.append(int(ll[1]))

In [2]:
def f(x):   # objective function
    return np.sum(p*x)

def g(x):   # constraint function
    return np.sum(w*x)

In [3]:
# testing f(x) and g(x):
x = np.random.randint(2, size=numOfItems)
print('x:')
print(x)
print('p*x:')
print(p*x)
print('f(x) = %d (profit)' % f(x))
print('-------')
print('w*x:')
print(w*x)
print('g(x) = %d (weight)' % g(x))
print('-------')
print('W = %d' % W)
if g(x) <= W:
    print('feasible')
else:
    print('infeasible')

x:
[0 0 0 1 1 0 0 0 0 1 0 0 0 1 0 0 0 0 0 0]
p*x:
[ 0  0  0 65 70  0  0  0  0 40  0  0  0 61  0  0  0  0  0  0]
f(x) = 236 (profit)
-------
w*x:
[ 0  0  0 41 69  0  0  0  0 64  0  0  0 79  0  0  0  0  0  0]
g(x) = 253 (weight)
-------
W = 500
feasible


In [4]:
# Part I: brute-force algorithm:

tic = time.time()

f_bestsofar = -np.infty
solution_bestsofar = []

# create and evaluate all bitstrings of length n
for i in xrange(0,2**numOfItems):
    # conversion from integer to binary representation as numpy array:
    x = np.array([int(j) for j in np.binary_repr(i, numOfItems)])
    
    # if new solution better than best so far & feasible, keep it
    if f(x) > f_bestsofar and g(x) <= W:
        f_bestsofar = f(x)
        solution_bestsofar = x

        
print('best found f-value: %d' % f_bestsofar)
print('best solution found: ')
print(solution_bestsofar)
print('-------')
print(p)
print(w)

toc = time.time()
t_bruteforce = toc - tic
print('%e sec elapsed' % (toc - tic))

best found f-value: 740
best solution found: 
[1 1 0 1 0 1 1 1 0 0 0 1 1 0 1 0 1 1 1 0]
-------
[67, 63, 52, 65, 70, 78, 71, 57, 24, 40, 35, 56, 70, 61, 80, 36, 59, 25, 49, 44]
[37, 20, 72, 41, 69, 55, 44, 59, 64, 64, 55, 47, 66, 79, 32, 44, 31, 28, 33, 68]
2.154623e+01 sec elapsed


In [5]:
# Part II: dynamic programming
#
# a) P(i, j): only items from 1:i are allowed and the knapsack is restricted to j
# b) entire problem solved if P(numOfItems, W) is solved
# c) P(i, j) = max {P(i-1, j), P(i-1, j-w_i)+p_i }

In [5]:
# recursive implementation:

def P_rec(i, j):
    '''
       Recursive implementation of the Bellman equation
       for the 0-1 knapsack problem when
       only the first i items are allowed and the knapsack
       is restricted to a weight of j.
       
       Note that i goes from 0 to numOfItems-1 here.
    '''
    if j <= 0:
        return 0
    if i == 0:
        if w[i] <= j:
            return p[i]
        else:
            return 0
    else:
        return max(P_rec(i-1, j), P_rec(i-1, j-w[i]) + p[i])
        

In [6]:
tic = time.time()

print(P_rec(numOfItems-1, W))

toc = time.time()
t_recursive = toc - tic
print('%e sec elapsed' % (toc - tic))

740
2.910168e-01 sec elapsed


In [7]:
# non-recursive implementation:

# Note: indices always start from 0
#       i.e. here, the row entry i, belongs to the (i+1)th item
#       and column j corresponds to weight j+1 !!!

tic = time.time()

# create empty array first:
P = np.zeros((numOfItems, W))
# init for first item:
for j in range(0, W):
    if j+1 >= w[0]: # does first item fit the knapsack of size j?
        P[0][j] = p[0]
        
# go through table row by row and compute entries according to Bellman equality from II.c)
for i in range(1, numOfItems):
    for j in range(1, W):
        P[i][j] = max(P[i-1][j], 0 if j-w[i] < 0 else P[i-1][j-w[i]]+p[i])
        
print(P[numOfItems-1][W-1])

toc = time.time()
t_dynprog = toc - tic
print('%e sec elapsed' % (toc - tic))
print(P)

740.0
2.600193e-02 sec elapsed
[[   0.    0.    0. ...,   67.   67.   67.]
 [   0.    0.    0. ...,  130.  130.  130.]
 [   0.    0.    0. ...,  182.  182.  182.]
 ..., 
 [   0.    0.    0. ...,  716.  716.  716.]
 [   0.    0.    0. ...,  740.  740.  740.]
 [   0.    0.    0. ...,  740.  740.  740.]]


In [8]:
# non-recursive implementation:

tic = time.time()

# create empty array first
# hence, explicit init. for i=0 and j=0 not needed
P = np.zeros((numOfItems+1, W+1))

# init for first item:
for j in range(0, W+1):
    if j >= w[0]: # does first item fit the knapsack of size i?
        P[1][j] = p[0]
        
# go through table row by row and compute entries according to Bellman equality from II.c)
for i in range(2, numOfItems+1):
    for j in range(1, W+1):
        P[i][j] = max(P[i-1][j], 0 if j-w[i-1] < 0 else p[i-1] + P[i-1][j-w[i-1]])
        
print(P[numOfItems][W])

toc = time.time()
t_dynprog = toc - tic
print('%e sec elapsed' % (toc - tic))
print(P)

740.0
1.700115e-02 sec elapsed
[[   0.    0.    0. ...,    0.    0.    0.]
 [   0.    0.    0. ...,   67.   67.   67.]
 [   0.    0.    0. ...,  130.  130.  130.]
 ..., 
 [   0.    0.    0. ...,  716.  716.  716.]
 [   0.    0.    0. ...,  740.  740.  740.]
 [   0.    0.    0. ...,  740.  740.  740.]]


In [9]:
print('times elapsed for the different algorithms:')
print('brute force:      %e' % t_bruteforce)
print('recursive algo.:  %e' % t_recursive)
print('dyn. programming: %e' % t_dynprog)

times elapsed for the different algorithms:
brute force:      2.154623e+01
recursive algo.:  2.910168e-01
dyn. programming: 1.700115e-02


In [253]:
# results on instance 3 (in sec, only 1 run):
#                       10D           20D           30D
# brute force       8.100009e-02  8.165600e+01  out of memory
# recursive algo.   1.000166e-03  4.080000e-01  2.832830e+02 (> 4.5 min)
# dyn. programming  8.999825e-03  3.500009e-02  8.599997e-02

In [10]:
# dynamic programming implementation, computing also the optimal solution:

# Note: indices again start always from 0
#       i.e. here, the row entry i, belongs to the (i+1)th item
#       and column j corresponds to a weight of j+1 !!!


tic = time.time()
# create empty arrays first:
P = np.zeros((numOfItems, W)) # optimal profit when items 1, ..., i used and knapsack weight is j
S = np.zeros((numOfItems, W)) # stores whether item i is used for subproblem P(i,j)
# init for first item:
for j in range(0, W):
    if j+1 >= w[0]: # does first item fit the knapsack of size j+1?
        P[0][j] = p[0]
        S[0][j] = 1
        
# go through table row by row and compute entries according to Bellman equality from II.c)
for i in range(1, numOfItems):
    for j in range(1, W):
        # set P[i][j] = max(P[i-1][j], 
        #                   0 if j-w[k] < 0 else P[i-1][j-w[i]]+p[i])
        # and S[i][j] correspondingly
        if P[i-1][j] > (0 if j-w[i] < 0 else P[i-1][j-w[i]]+p[i]):
            # better to not take item i
            P[i][j] = P[i-1][j] 
            S[i][j] = 0
        else:
            if j-w[i] < 0:
                P[i][j] = 0
                S[i][j] = 0
            else:
                P[i][j] = P[i-1][j-w[i]]+p[i]
                S[i][j] = 1 
        
# retrieve optimal solution
i = numOfItems
j = W
optsol = np.zeros(numOfItems)
while i >= 1:
    optsol[i-1] = S[i-1][j-1]
    if S[i-1][j-1] == 1:
        j = j - w[i-1]
    i = i-1


print('optimal f-value found: %d' % P[numOfItems-1][W-1])
print('optimal solution found: ')
print(optsol)
print('-------')
print(p)
print(w)

toc = time.time()
t_bruteforce = toc - tic
print('%e sec elapsed' % (toc - tic))




optimal f-value found: 740
optimal solution found: 
[ 1.  1.  0.  1.  0.  1.  1.  1.  0.  0.  0.  1.  1.  0.  1.  0.  1.  1.
  1.  0.]
-------
[67, 63, 52, 65, 70, 78, 71, 57, 24, 40, 35, 56, 70, 61, 80, 36, 59, 25, 49, 44]
[37, 20, 72, 41, 69, 55, 44, 59, 64, 64, 55, 47, 66, 79, 32, 44, 31, 28, 33, 68]
3.700185e-02 sec elapsed
